In [1]:
!pip install gdown
!pip install unrar
!pip install pesq

!pip install speechbrain
!pip install torchaudio


  Preparing metadata (setup.py) ... done
  Created wheel for pesq: filename=pesq-0.0.4-cp310-cp310-linux_x86_64.whl size=262968 sha256=55941de4d8bc57093e4b9845d47daf7d766ffbae498545db1dd338a7f12e90a4
  Stored in directory: /root/.cache/pip/wheels/c5/4e/2c/251524370c0fdd659e99639a0fbd0ca5a782c3aafcd456b28d
Successfully built pesq
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using ca

first model

In [2]:
import torch

print("CUDA available:", torch.cuda.is_available())


CUDA available: True


In [11]:
import gdown

# Full link: https://drive.google.com/file/d/1wjAMOe2sEWMCSUjz8nfXJCAhDHHmLDhr/view?usp=drive_link
file_id = '1wjAMOe2sEWMCSUjz8nfXJCAhDHHmLDhr'
url = f'https://drive.google.com/uc?id={file_id}'

output = 'data.rar'
gdown.download(url, output, quiet=False)


Downloading...
From (original): https://drive.google.com/uc?id=1wjAMOe2sEWMCSUjz8nfXJCAhDHHmLDhr
From (redirected): https://drive.google.com/uc?id=1wjAMOe2sEWMCSUjz8nfXJCAhDHHmLDhr&confirm=t&uuid=4280861b-bc48-4963-836d-b05f6b3a5377
To: /content/data.rar
100%|██████████| 77.9M/77.9M [00:00<00:00, 146MB/s]


'data.rar'

In [12]:
! du -h data.rar

75M	data.rar


In [13]:
!unrar x data.rar


UNRAR 6.11 beta 1 freeware      Copyright (c) 1993-2022 Alexander Roshal


Extracting from data.rar

Creating    dataset                                                   OK
Creating    dataset/clean                                             OK
Extracting  dataset/clean/0-0-fa.wav                                       0%  OK 
Extracting  dataset/clean/1-1-fa.wav                                       0%  OK 
Extracting  dataset/clean/1-2-fa.wav                                       0%  OK 
Extracting  dataset/clean/1-3-fa.wav                                       0%  OK 
Extracting  dataset/clean/1-4-fa.wav                                       1%  OK 
Extracting  dataset/clean/1-5-fa.wav                                       1%  OK 
Extracting  dataset/clean/1-6-fa.wav                                       1%  OK 
Extracting  dataset/clean/2-1-fa.wav                                       2%  OK 
Extracting  data

In [14]:
import os
import torch
import torchaudio
from torch.utils.data import Dataset, DataLoader

class SpeechDataset(Dataset):
    def __init__(self, clean_dir, noisy_dir, sr=16000):
        self.clean_files = [os.path.join(clean_dir, f) for f in os.listdir(clean_dir) if f.endswith('.wav')]
        self.noisy_files = [os.path.join(noisy_dir, f) for f in os.listdir(noisy_dir) if f.endswith('.m4a')]
        self.sr = sr
        self.length = sr * 3

    def __len__(self):
        return len(self.clean_files)

    def __getitem__(self, idx):
        clean, sr = torchaudio.load(self.clean_files[idx])
        noisy, sr = torchaudio.load(self.noisy_files[idx])

        clean = torchaudio.transforms.Resample(sr, self.sr)(clean)
        noisy = torchaudio.transforms.Resample(sr, self.sr)(noisy)

        clean = self._adjust_length(clean)
        noisy = self._adjust_length(noisy)

        return noisy.squeeze(0), clean.squeeze(0)

    def _adjust_length(self, waveform):
        if waveform.size(1) > self.length:
            return waveform[:, :self.length]
        else:
            pad_amount = self.length - waveform.size(1)
            return torch.nn.functional.pad(waveform, (0, pad_amount))

clean_dir = '/content/dataset/clean'
noisy_dir = '/content/dataset/noisy'
dataset = SpeechDataset(clean_dir, noisy_dir)
dataloader = DataLoader(dataset, batch_size=32, shuffle=True)


In [15]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
import torch.nn as nn
import torch.optim as optim

class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.encoder = nn.Sequential(
            nn.Conv1d(1, 16, kernel_size=15, stride=1, padding=7),
            nn.ReLU(),
            nn.Conv1d(16, 32, kernel_size=15, stride=1, padding=7),
            nn.ReLU(),
            nn.Conv1d(32, 64, kernel_size=15, stride=1, padding=7),
            nn.ReLU()
        )
        self.decoder = nn.Sequential(
            nn.ConvTranspose1d(64, 32, kernel_size=15, stride=1, padding=7),
            nn.ReLU(),
            nn.ConvTranspose1d(32, 16, kernel_size=15, stride=1, padding=7),
            nn.ReLU(),
            nn.ConvTranspose1d(16, 1, kernel_size=15, stride=1, padding=7),
            nn.Tanh()
        )

    def forward(self, x):
        x = self.encoder(x)
        x = self.decoder(x)
        return x

class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        self.net = nn.Sequential(
            nn.Conv1d(1, 16, kernel_size=15, stride=1, padding=7),
            nn.LeakyReLU(0.2),
            nn.Conv1d(16, 32, kernel_size=15, stride=1, padding=7),
            nn.LeakyReLU(0.2),
            nn.Conv1d(32, 64, kernel_size=15, stride=1, padding=7),
            nn.LeakyReLU(0.2),
            nn.Conv1d(64, 1, kernel_size=15, stride=1, padding=7)
        )

    def forward(self, x):
        return self.net(x)

generator = Generator().to(device)
discriminator = Discriminator().to(device)
criterion = nn.MSELoss()
optimizer_G = optim.Adam(generator.parameters(), lr=0.0002)
optimizer_D = optim.Adam(discriminator.parameters(), lr=0.0002)

num_epochs = 50

for epoch in range(num_epochs):
    for i, (noisy, clean) in enumerate(dataloader):
        noisy, clean = noisy.unsqueeze(1).to(device), clean.unsqueeze(1).to(device)  # Add channel dimension

        optimizer_D.zero_grad()
        output = generator(noisy)
        loss_D_real = criterion(discriminator(clean), torch.ones_like(discriminator(clean)).to(device))
        loss_D_fake = criterion(discriminator(output.detach()), torch.zeros_like(discriminator(output.detach())).to(device))
        loss_D = (loss_D_real + loss_D_fake) / 2
        loss_D.backward()
        optimizer_D.step()

        optimizer_G.zero_grad()
        loss_G = criterion(discriminator(output), torch.ones_like(discriminator(output)).to(device))
        loss_G.backward()
        optimizer_G.step()

        if i % 10 == 0:
            print(f"Epoch [{epoch}/{num_epochs}], Step [{i}/{len(dataloader)}], Loss D: {loss_D.item()}, Loss G: {loss_G.item()}")


Epoch [0/50], Step [0/4], Loss D: 0.5172184705734253, Loss G: 1.0031746625900269
Epoch [1/50], Step [0/4], Loss D: 0.47343671321868896, Loss G: 0.9193388819694519
Epoch [2/50], Step [0/4], Loss D: 0.43299511075019836, Loss G: 0.8244279623031616
Epoch [3/50], Step [0/4], Loss D: 0.3858546316623688, Loss G: 0.7051727771759033
Epoch [4/50], Step [0/4], Loss D: 0.32750403881073, Loss G: 0.5595012903213501
Epoch [5/50], Step [0/4], Loss D: 0.2498687505722046, Loss G: 0.5102494955062866
Epoch [6/50], Step [0/4], Loss D: 0.16053816676139832, Loss G: 0.49975407123565674
Epoch [7/50], Step [0/4], Loss D: 0.12063556909561157, Loss G: 0.3591078221797943
Epoch [8/50], Step [0/4], Loss D: 0.14741146564483643, Loss G: 0.24468231201171875
Epoch [9/50], Step [0/4], Loss D: 0.1424117088317871, Loss G: 0.27617979049682617
Epoch [10/50], Step [0/4], Loss D: 0.12097812443971634, Loss G: 0.37840574979782104
Epoch [11/50], Step [0/4], Loss D: 0.12273035943508148, Loss G: 0.4544849097728729
Epoch [12/50], St

In [ ]:
import torchaudio
import IPython.display as ipd

def denoise_audio(model, noisy_file_path, output_file_path, device):

    noisy, sr = torchaudio.load(noisy_file_path)


    noisy = noisy.to(device)


    noisy = noisy.unsqueeze(0)


    model.eval()
    with torch.no_grad():
        denoised = model(noisy)


    denoised = denoised.squeeze(0)


    denoised = denoised.cpu()
    torchaudio.save(output_file_path, denoised, sr)


    return ipd.Audio(output_file_path)


noisy_file_path = '/content/dataset/noisy/2-110.m4a'
output_file_path = '/content/denoised_file.wav'
path3="/content/dataset/clean/2-110-fa.wav"

audio_widget = denoise_audio(generator, noisy_file_path, output_file_path, device)
audio_widget2 = ipd.Audio(noisy_file_path)
audio_widget3 = ipd.Audio(path3)

ipd.display(audio_widget)
ipd.display(audio_widget2)
ipd.display(audio_widget3)


test metricGan model

In [ ]:
import torch
import torchaudio
from speechbrain.inference.enhancement import SpectralMaskEnhancement

enhance_model = SpectralMaskEnhancement.from_hparams(
    source="speechbrain/metricgan-plus-voicebank",
    savedir="pretrained_models/metricgan-plus-voicebank",
)


noisy = enhance_model.load_audio(
    "/content/dataset/noisy/2-110.m4a"
).unsqueeze(0)


enhanced = enhance_model.enhance_batch(noisy, lengths=torch.tensor([1.]))


torchaudio.save('/content/enhanced.wav', enhanced.cpu(), 16000)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


hyperparams.yaml:   0%|          | 0.00/1.12k [00:00<?, ?B/s]

enhance_model.ckpt:   0%|          | 0.00/7.59M [00:00<?, ?B/s]

In [ ]:
audio_widget2 = ipd.Audio("/content/dataset/noisy/2-110.m4a")
audio_widget3 = ipd.Audio('/content/enhanced.wav')

ipd.display(audio_widget2)
ipd.display(audio_widget3)

fine tune

In [32]:
import torch
import torchaudio
from speechbrain.inference.enhancement import SpectralMaskEnhancement


model = SpectralMaskEnhancement.from_hparams(
    source="speechbrain/metricgan-plus-voicebank",
    savedir="pretrained_models/metricgan-plus-voicebank"
)

# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device = torch.device("cpu")
model = model.to(device)


criterion = torch.nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-7)


In [33]:
device

device(type='cpu')

In [34]:
import os
import glob
import torch
import torchaudio
from torch.utils.data import DataLoader, Dataset


def getData(noisy_dir,clean_dir):
  noisy_files = sorted(glob.glob(os.path.join(noisy_dir, '*.m4a')))
  clean_files = sorted(glob.glob(os.path.join(clean_dir, '*.wav')))
  # print(len(noisy_files))
  # print(noisy_files)
  # print(len(clean_files))
  # print(clean_files)
  return noisy_files,clean_files

class CustomDataset(Dataset):
    def __init__(self, noisy_dir, clean_dir):
        self.noisy_files = sorted(glob.glob(os.path.join(noisy_dir, '*.m4a')))
        self.clean_files = sorted(glob.glob(os.path.join(clean_dir, '*.wav')))
        assert len(self.noisy_files) == len(self.clean_files), "Mismatch between noisy and clean files"

    def __len__(self):
        return len(self.noisy_files)

    def __getitem__(self, idx):
        noisy = torchaudio.load(self.noisy_files[idx])[0].to(device)
        clean = torchaudio.load(self.clean_files[idx])[0].to(device)
        return noisy, clean


noisy_dir = '/content/dataset/noisy'
clean_dir = '/content/dataset/clean'

noisy_files,clean_files=getData(noisy_dir,clean_dir)

dataset = CustomDataset(noisy_dir, clean_dir)
dataloader = DataLoader(dataset, batch_size=1, shuffle=True)

print(len(noisy_files))
# print(noisy_files)
print(len(clean_files))
# print(clean_files)


122
122


In [ ]:
def pad_or_crop(tensor, length):
    if tensor.size(1) > length:
        return tensor[:, :length]
    elif tensor.size(1) < length:
        padding = length - tensor.size(1)
        return torch.nn.functional.pad(tensor, (0, padding))
    else:
        return tensor

for param in model.parameters():
    param.requires_grad = True

num_epochs = 2

for epoch in range(num_epochs):
    model.train()
    epoch_loss = 0

    for i in range(len(noisy_files)):
        noisy, clean = noisy_files[i], clean_files[i]
        # lengths = torch.tensor([noisy.size(1)]).float().to(device)
        # enhanced = model.enhance_batch(noisy, lengths)
        noisy = model.load_audio(
            noisy
        ).unsqueeze(0)
        clean = model.load_audio(
            clean
        ).unsqueeze(0)
        target_length = clean.size(1)
        # print(target_length)
        noisy = pad_or_crop(noisy, target_length)
        clean = pad_or_crop(clean, target_length)
        enhanced = model.enhance_batch(noisy, lengths=torch.tensor([1.]))
        enhanced = pad_or_crop(enhanced, target_length)
        loss = criterion(enhanced, clean)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        epoch_loss += loss.item()
    print(f"Epoch {epoch+1}/{num_epochs}, Loss: {epoch_loss/len(dataloader)}")

torch.save(model.state_dict(), 'fine_tuned_spectral_mask_enhancement.pth')

Epoch 1/2, Loss: 0.009234164581924189
Epoch 2/2, Loss: 0.009215251374684397


In [36]:
# model = SpectralMaskEnhancement.from_hparams(
#     source="speechbrain/metricgan-plus-voicebank",
#     savedir="pretrained_models/metricgan-plus-voicebank"
# )
# model.load_state_dict(torch.load('fine_tuned_spectral_mask_enhancement.pth'))
# model = model.to(device)

# noisy = model.load_audio(
#     "/content/dataset/noisy/2-94.m4a"
# ).unsqueeze(0)

# enhanced = model.enhance_batch(noisy, lengths=torch.tensor([1.]))

# torchaudio.save('/content/enhanced.wav', enhanced.cpu(), 16000)


In [38]:
pip install pydub

In [39]:
from pydub import AudioSegment
import os

def convert_m4a_to_wav_and_delete(directory_path):
    # Iterate through all files in the directory
    for filename in os.listdir(directory_path):
        if filename.endswith(".m4a"):
            # Construct the full file path
            file_path = os.path.join(directory_path, filename)

            # Load the M4A file
            audio = AudioSegment.from_file(file_path, format="m4a")

            # Extract the base name (without extension) for the new WAV file
            base_name = os.path.splitext(filename)[0]

            # Create the new WAV file path
            wav_file_path = os.path.join(directory_path, f"{base_name}.wav")

            # Export the audio in WAV format
            audio.export(wav_file_path, format="wav")

            # Check if the WAV file was successfully created
            if os.path.exists(wav_file_path):
                # Delete the original M4A file
                os.remove(file_path)
                print(f"M4A file '{file_path}' deleted successfully after conversion.")
            else:
                print(f"WAV file '{wav_file_path}' could not be created. Skipping deletion of M4A file '{file_path}'.")

# Example usage
directory_path = 'dataset/noisy'
convert_m4a_to_wav_and_delete(directory_path)
print("Conversion and deletion process complete.")


M4A file 'dataset/noisy/2-33-qu.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-56.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-18.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-60-gp.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-87-q4.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-23-bat.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/0-0.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-34.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-19-fa-sn.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-49-6t.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-28-po.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-38.m4a' deleted successfully after conversion.
M4A file 'dataset/noisy/2-13-fa-qp.m4a' deleted successfully after conversion.
M4A file 'dataset/noi

In [41]:
import os
import torch
import torchaudio

# Define the enhancement model and load fine-tuned weights
model = SpectralMaskEnhancement.from_hparams(
    source="speechbrain/metricgan-plus-voicebank",
    savedir="pretrained_models/metricgan-plus-voicebank"
)
model.load_state_dict(torch.load('fine_tuned_spectral_mask_enhancement.pth'))
model = model.to(device)

def enhance_directory(input_dir, output_dir, sample_rate=16000):
    # Create the output directory if it doesn't exist
    os.makedirs(output_dir, exist_ok=True)

    # Process each file in the input directory
    for filename in os.listdir(input_dir):
        if filename.endswith('.wav'):
            # Load the noisy audio file
            file_path = os.path.join(input_dir, filename)
            noisy = model.load_audio(file_path).unsqueeze(0)

            # Enhance the audio
            enhanced = model.enhance_batch(noisy, lengths=torch.tensor([1.]))

            # Save the enhanced audio file
            output_path = os.path.join(output_dir, filename)
            torchaudio.save(output_path, enhanced.cpu(), sample_rate)
            print(f"Enhanced audio saved to: {output_path}")

# Example usage
input_directory = '/content/dataset/noisy'
output_directory = '/content/dataset/enhanced'
enhance_directory(input_directory, output_directory)


Enhanced audio saved to: /content/dataset/enhanced/2-23-ap.wav
Enhanced audio saved to: /content/dataset/enhanced/2-90-4m.wav
Enhanced audio saved to: /content/dataset/enhanced/2-14.wav
Enhanced audio saved to: /content/dataset/enhanced/2-25-bq.wav
Enhanced audio saved to: /content/dataset/enhanced/2-21.wav
Enhanced audio saved to: /content/dataset/enhanced/2-8.wav
Enhanced audio saved to: /content/dataset/enhanced/2-93-9i.wav
Enhanced audio saved to: /content/dataset/enhanced/2-93-1a.wav
Enhanced audio saved to: /content/dataset/enhanced/2-29-cb.wav
Enhanced audio saved to: /content/dataset/enhanced/1-5.wav
Enhanced audio saved to: /content/dataset/enhanced/2-60-gp.wav
Enhanced audio saved to: /content/dataset/enhanced/2-94.wav
Enhanced audio saved to: /content/dataset/enhanced/2-20-s7.wav
Enhanced audio saved to: /content/dataset/enhanced/2-108.wav
Enhanced audio saved to: /content/dataset/enhanced/0-0.wav
Enhanced audio saved to: /content/dataset/enhanced/2-80.wav
Enhanced audio sav

In [42]:
! pip install pesq

In [43]:
import os
import numpy as np
from scipy.io import wavfile
from scipy.signal import resample
from pesq import pesq, PesqError

def read_and_resample(filepath, target_sample_rate):
    sr, audio = wavfile.read(filepath)
    if sr != target_sample_rate:
        # Calculate the number of samples after resampling
        num_samples = round(len(audio) * float(target_sample_rate) / sr)
        audio = resample(audio, num_samples)
    return audio

def calculate_pesq(clean_dir, denoised_dir, sample_rate=16000):
    pesq_scores = []

    clean_files = sorted(os.listdir(clean_dir))
    denoised_files = sorted(os.listdir(denoised_dir))

    for clean_file, denoised_file in zip(clean_files, denoised_files):
        clean_path = os.path.join(clean_dir, clean_file)
        denoised_path = os.path.join(denoised_dir, denoised_file)

        if os.path.isfile(clean_path) and os.path.isfile(denoised_path):
            try:
                # Read and resample the wav files
                clean_audio = read_and_resample(clean_path, sample_rate)
                denoised_audio = read_and_resample(denoised_path, sample_rate)

                # Calculate PESQ score
                score = pesq(sample_rate, clean_audio, denoised_audio, 'wb')
                pesq_scores.append(score)
                print(f'File: {clean_file}, PESQ: {score}')
            except PesqError as e:
                print(f"Error calculating PESQ for {clean_file} and {denoised_file}: {e}")
            except Exception as e:
                print(f"Error processing {clean_file} and {denoised_file}: {e}")

    return pesq_scores

if __name__ == "__main__":
    clean_dir = '/content/dataset/clean'
    denoised_dir = '/content/dataset/enhanced'
    pesq_scores = calculate_pesq(clean_dir, denoised_dir)
    if pesq_scores:
        print(f'Average PESQ Score: {np.mean(pesq_scores)}')
    else:
        print('No PESQ scores calculated.')


File: 0-0-fa.wav, PESQ: 1.3235549926757812
File: 1-1-fa.wav, PESQ: 1.1342782974243164
File: 1-2-fa.wav, PESQ: 1.1773464679718018
File: 1-3-fa.wav, PESQ: 1.0198487043380737
File: 1-4-fa.wav, PESQ: 1.1282882690429688
File: 1-5-fa.wav, PESQ: 1.0993577241897583
File: 1-6-fa.wav, PESQ: 1.057254672050476
File: 2-1-fa.wav, PESQ: 1.056046485900879
File: 2-10-fa.wav, PESQ: 1.0672787427902222
File: 2-104-fa-1hjo92mg2e.wav, PESQ: 1.021232008934021
File: 2-104-fa-a9o255k5afo.wav, PESQ: 1.0398002862930298
File: 2-104-fa-do3d8akeuek.wav, PESQ: 1.0416114330291748
File: 2-104-fa-obf721ivs0c.wav, PESQ: 1.0274784564971924
File: 2-106-fa.wav, PESQ: 1.0533949136734009
File: 2-108-fa.wav, PESQ: 1.0538005828857422
File: 2-11-fa.wav, PESQ: 1.0657837390899658
File: 2-110-fa.wav, PESQ: 1.048046350479126
File: 2-12-fa.wav, PESQ: 1.0677076578140259
File: 2-13-fa-lnjrak25fbg.wav, PESQ: 1.0907866954803467
File: 2-13-fa-qplgmvtr048.wav, PESQ: 1.063726544380188
File: 2-14-fa.wav, PESQ: 1.0914244651794434
File: 2-15-

In [ ]:
import torch
import torchaudio
import IPython.display as ipd

audio_widget2 = ipd.Audio("/content/dataset/noisy/2-94.m4a")
audio_widget3 = ipd.Audio('/content/enhanced.wav')

ipd.display(audio_widget2)
ipd.display(audio_widget3)